In [9]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [10]:
# Load Packages
import jax.numpy as jnp
from plotly.subplots import make_subplots

# Load Custom Modules
from plots import plot_true_function, add_optimization_path
from core import optimize_function, initial_point
from problems import get_function_by_name

In [11]:
# Define Constants
X_MIN, X_MAX, X_POINTS = -10, 10, 100
Y_MIN, Y_MAX, Y_POINTS = -10, 10, 100

x = jnp.linspace(X_MIN, X_MAX, X_POINTS)
y = jnp.linspace(Y_MIN, Y_MAX, Y_POINTS)

# Randomly sample initial point
pi = initial_point(42, minval=-10, maxval=10)

# Set Seeds for generating random samples during optimization
seeds = [42, 42, 42, 42]

# Set Function
fn = get_function_by_name('ackleys')

# Set Noise Parameters - Cone
true_params = (0, 0, 1)
noise_params = (20, 20, 0.1)
meas_noise_params = (0, 500.0)


# Set Noise Parameters - Ackleys
true_params = (20, 0.2, 2*jnp.pi)
noise_params = [0.2*p for p in true_params]
meas_noise_params = (0, 1.0)

# Set Noise Parameters - Brannin
# true_params = (1, 5.1/(4*jnp.pi**2), 5/jnp.pi, 6, 10, 1/(8*jnp.pi))
# noise_params = [0.2*p for p in true_params]
# meas_noise_params = (0, 300.0)

batch_size = 3

# Set Gradient Agreement Filter
gaf_parameters = {
    'method': 'pairwise',
    # 'cos_dist_max': 1 - jnp.cos(10 / 180 * jnp.pi), # 0.97
    'cos_dist_max': 0.97,
    'max_retries_on_failure': 10
}

In [12]:
cfig = make_subplots(rows=2, cols=2, subplot_titles=['SGD', 'Adam', 'AdaGrad', 'SGD w/ Nesterov'])

# SGD
p_sgd = optimize_function(fn, pi, true_params, noise_params, steps=50, learning_rate=0.25, batch_size=batch_size, method='sgd', seed=seeds[0])
fig = plot_true_function(x, y, lambda x: fn(x, true_params))
fig.update_layout(title=f'SGD', title_x=0.5)
add_optimization_path(fig, p_sgd)
cfig.add_trace(fig.data[0], row=1, col=1)
cfig.add_trace(fig.data[1], row=1, col=1)

# Adam
p_adam = optimize_function(fn, pi, true_params, noise_params, steps=50, learning_rate=0.25, batch_size=batch_size, method='adam', seed=seeds[1])
fig = plot_true_function(x, y, lambda x: fn(x, true_params))
fig.update_layout(title=f'Adam', title_x=0.5)
add_optimization_path(fig, p_adam)
cfig.add_trace(fig.data[0], row=1, col=2)
cfig.add_trace(fig.data[1], row=1, col=2)

# AdaGrad
p_adagrad = optimize_function(fn, pi, true_params, noise_params, steps=50, learning_rate=0.25, batch_size=batch_size, method='adagrad', seed=seeds[2])
fig = plot_true_function(x, y, lambda x: fn(x, true_params))
fig.update_layout(title=f'AdaGrad', title_x=0.5)
add_optimization_path(fig, p_adagrad)
cfig.add_trace(fig.data[0], row=2, col=1)
cfig.add_trace(fig.data[1], row=2, col=1)

# RMSprop
p_sgd_nesterov = optimize_function(fn, pi, true_params, noise_params, steps=50, learning_rate=0.25, batch_size=batch_size,method='sgd', solver_params={'nesterov': True, 'momentum': 0.01}, seed=seeds[3])
fig = plot_true_function(x, y, lambda x: fn(x, true_params))
fig.update_layout(title=f'SGD w/ Nesterov', title_x=0.5)
add_optimization_path(fig, p_sgd_nesterov)
cfig.add_trace(fig.data[0], row=2, col=2)
cfig.add_trace(fig.data[1], row=2, col=2)

cfig.update_layout(height=1000, width=1000, title_text='Optimization Algorithms without GAF', title_x=0.5)
cfig.show()


In [13]:
cfig = make_subplots(rows=2, cols=2, subplot_titles=['SGD', 'Adam', 'AdaGrad', 'SGD w/ Nesterov'])

# SGD
p_sgd_gaf = optimize_function(fn, pi, true_params, noise_params, steps=50, learning_rate=0.25, batch_size=batch_size, method='sgd', gaf_params=gaf_parameters, seed=seeds[0])
fig = plot_true_function(x, y, lambda x: fn(x, true_params))
fig.update_layout(title=f'SGD', title_x=0.5)
add_optimization_path(fig, p_sgd_gaf)
cfig.add_trace(fig.data[0], row=1, col=1)
cfig.add_trace(fig.data[1], row=1, col=1)

# Adam
p_adam_gaf = optimize_function(fn, pi, true_params, noise_params, steps=50, learning_rate=0.25, batch_size=batch_size, method='adam', gaf_params=gaf_parameters, seed=seeds[1])
fig = plot_true_function(x, y, lambda x: fn(x, true_params))
fig.update_layout(title=f'Adam', title_x=0.5)
add_optimization_path(fig, p_adam_gaf)
cfig.add_trace(fig.data[0], row=1, col=2)
cfig.add_trace(fig.data[1], row=1, col=2)

# AdaGrad
p_adagrad_gaf = optimize_function(fn, pi, true_params, noise_params, steps=50, learning_rate=0.25, batch_size=batch_size, method='adagrad', gaf_params=gaf_parameters, seed=seeds[2])
fig = plot_true_function(x, y, lambda x: fn(x, true_params))
fig.update_layout(title=f'AdaGrad', title_x=0.5)
add_optimization_path(fig, p_adagrad_gaf)
cfig.add_trace(fig.data[0], row=2, col=1)
cfig.add_trace(fig.data[1], row=2, col=1)

# RMSProp
p_sgd_nesterov_gad = optimize_function(fn, pi, true_params, noise_params, steps=50, learning_rate=0.25, batch_size=batch_size, method='sgd', solver_params={'nesterov': True, 'momentum': 0.01}, gaf_params=gaf_parameters, seed=seeds[3])
fig = plot_true_function(x, y, lambda x: fn(x, true_params))
fig.update_layout(title=f'SGD w/ Nesterov', title_x=0.5)
add_optimization_path(fig, p_sgd_nesterov_gad)
cfig.add_trace(fig.data[0], row=2, col=2)
cfig.add_trace(fig.data[1], row=2, col=2)

cfig.update_layout(height=1000, width=1000, title_text='Optimization Algorithms w/ GAF', title_x=0.5)
cfig.show()


In [14]:
cfig = make_subplots(rows=2, cols=2, subplot_titles=['SGD', 'Adam', 'AdaGrad', 'SGD w/ Nesterov'])

# SGD
p_sgd_gaf = optimize_function(fn, pi, true_params, (0., 0., 0.), meas_noise_params=meas_noise_params, steps=50, learning_rate=0.25, batch_size=batch_size, method='sgd', seed=seeds[0])
fig = plot_true_function(x, y, lambda x: fn(x, true_params))
fig.update_layout(title=f'SGD', title_x=0.5)
add_optimization_path(fig, p_sgd_gaf)
cfig.add_trace(fig.data[0], row=1, col=1)
cfig.add_trace(fig.data[1], row=1, col=1)

# Adam
p_adam_gaf = optimize_function(fn, pi, true_params, (0., 0., 0.), meas_noise_params=meas_noise_params, steps=50, learning_rate=0.25, batch_size=batch_size, method='adam', seed=seeds[1])
fig = plot_true_function(x, y, lambda x: fn(x, true_params))
fig.update_layout(title=f'Adam', title_x=0.5)
add_optimization_path(fig, p_adam_gaf)
cfig.add_trace(fig.data[0], row=1, col=2)
cfig.add_trace(fig.data[1], row=1, col=2)

# AdaGrad
p_adagrad_gaf = optimize_function(fn, pi, true_params, (0., 0., 0.), meas_noise_params=meas_noise_params, steps=50, learning_rate=0.25, batch_size=batch_size, method='adagrad', seed=seeds[2])
fig = plot_true_function(x, y, lambda x: fn(x, true_params))
fig.update_layout(title=f'AdaGrad', title_x=0.5)
add_optimization_path(fig, p_adagrad_gaf)
cfig.add_trace(fig.data[0], row=2, col=1)
cfig.add_trace(fig.data[1], row=2, col=1)

# RMSProp
p_sgd_nesterov_gad = optimize_function(fn, pi, true_params, (0., 0., 0.), meas_noise_params=meas_noise_params, steps=50, learning_rate=0.25, batch_size=batch_size, method='sgd', solver_params={'nesterov': True, 'momentum': 0.01}, seed=seeds[3])
fig = plot_true_function(x, y, lambda x: fn(x, true_params))
fig.update_layout(title=f'SGD w/ Nesterov', title_x=0.5)
add_optimization_path(fig, p_sgd_nesterov_gad)
cfig.add_trace(fig.data[0], row=2, col=2)
cfig.add_trace(fig.data[1], row=2, col=2)

cfig.update_layout(height=1000, width=1000, title_text='Optimization Algorithms + Meas Noise', title_x=0.5)
cfig.show()

In [15]:
cfig = make_subplots(rows=2, cols=2, subplot_titles=['SGD', 'Adam', 'AdaGrad', 'SGD w/ Nesterov'])

# SGD
p_sgd_gaf = optimize_function(fn, pi, true_params, (0., 0., 0.), meas_noise_params=meas_noise_params, steps=50, learning_rate=0.25, batch_size=batch_size, method='sgd', gaf_params=gaf_parameters, seed=seeds[0])
fig = plot_true_function(x, y, lambda x: fn(x, true_params))
fig.update_layout(title=f'SGD', title_x=0.5)
add_optimization_path(fig, p_sgd_gaf)
cfig.add_trace(fig.data[0], row=1, col=1)
cfig.add_trace(fig.data[1], row=1, col=1)

# Adam
p_adam_gaf = optimize_function(fn, pi, true_params, (0., 0., 0.), meas_noise_params=meas_noise_params, steps=50, learning_rate=0.25, batch_size=batch_size, method='adam', gaf_params=gaf_parameters, seed=seeds[1])
fig = plot_true_function(x, y, lambda x: fn(x, true_params))
fig.update_layout(title=f'Adam', title_x=0.5)
add_optimization_path(fig, p_adam_gaf)
cfig.add_trace(fig.data[0], row=1, col=2)
cfig.add_trace(fig.data[1], row=1, col=2)

# AdaGrad
p_adagrad_gaf = optimize_function(fn, pi, true_params, (0., 0., 0.), meas_noise_params=meas_noise_params, steps=50, learning_rate=0.25, batch_size=batch_size, method='adagrad', gaf_params=gaf_parameters, seed=seeds[2])
fig = plot_true_function(x, y, lambda x: fn(x, true_params))
fig.update_layout(title=f'AdaGrad', title_x=0.5)
add_optimization_path(fig, p_adagrad_gaf)
cfig.add_trace(fig.data[0], row=2, col=1)
cfig.add_trace(fig.data[1], row=2, col=1)

# RMSProp
p_sgd_nesterov_gad = optimize_function(fn, pi, true_params, (0., 0., 0.), meas_noise_params=meas_noise_params, steps=50, learning_rate=0.25, batch_size=batch_size, method='sgd', solver_params={'nesterov': True, 'momentum': 0.01}, gaf_params=gaf_parameters, seed=seeds[3])
fig = plot_true_function(x, y, lambda x: fn(x, true_params))
fig.update_layout(title=f'SGD w/ Nesterov', title_x=0.5)
add_optimization_path(fig, p_sgd_nesterov_gad)
cfig.add_trace(fig.data[0], row=2, col=2)
cfig.add_trace(fig.data[1], row=2, col=2)

cfig.update_layout(height=1000, width=1000, title_text='Optimization Algorithms + Meas Noise w/ GAF', title_x=0.5)
cfig.show()